In [27]:
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.chrome.options import Options
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.action_chains import ActionChains
import time
from bs4 import BeautifulSoup
from urllib.request import urlopen
import pandas as pd
from glob import glob
from selenium.webdriver.common.keys import Keys

options= webdriver.ChromeOptions()

prefs={'download.default_directory':'/home/sang/dev_ws/eda/data',
       'download.prompt_for_download':False}
options.add_experimental_option('prefs',prefs)

url='https://www.saramin.co.kr/zf_user/'
driver=webdriver.Chrome(service=Service('../driver/chromedriver/chromedriver'),
                        options=options)

driver.get(url)

driver.find_element(By.CLASS_NAME,'btn_sign.signin').click()

input_id=driver.find_element(By.ID,'id')
input_password=driver.find_element(By.ID,'password')
input_id.click()
input_id.send_keys('hinoonyaso')
input_password.send_keys('ns55904498!')

login=driver.find_element(By.CLASS_NAME,'btn_login.BtnType.SizeML').click()

driver.find_element(By.CLASS_NAME,'Lbl').click()
driver.find_element(By.CLASS_NAME,'btn_no_view.btn_layer_close').click()

driver.find_element(By.CLASS_NAME,'ci').click()

driver.find_element(By.CLASS_NAME,'btn_search').click()
search=driver.find_element(By.CSS_SELECTOR,'#ipt_keyword_recruit')
search.send_keys('로봇 SW 개발')
driver.find_element(By.ID,'btn_search_recruit').click()
company=driver.find_element(By.CSS_SELECTOR,'#content > ul.tab_search_result.on > li:nth-child(3) > a')
company.click()

In [28]:
count=driver.find_element(By.CLASS_NAME,'cnt_result').text
start=count.find(' ')
end=count.find('건')
count=int(count[start:end])
count=int(count/20)+1
address=[]
uni_avg_list = []
corp_name_list = []
all_age=[]
all_salary=[]

for i in range(1, count+1):
    url = 'https://www.saramin.co.kr/zf_user/search/company?searchword=%EB%A1%9C%EB%B4%87+SW+%EA%B0%9C%EB%B0%9C&page={}&searchType=search&pageCount=20&mainSearch=n'.format(i)
    driver.get(url)
    driver.switch_to.window(driver.window_handles[0])
    company_info=driver.find_element(By.ID,'company_info')
    for i in driver.find_elements(By.CLASS_NAME,'company_popup'):
            print(i.text)
            corp_name_list.append(i.text)
    for idx,company in enumerate(company_info.find_elements(By.CLASS_NAME,'corp_info')):
        for info in company.find_elements(By.TAG_NAME,'dl'):
            if info.find_element(By.TAG_NAME,'dt').text == '기업주소':
                ads=info.find_element(By.TAG_NAME,'dd').text
                print(info.find_element(By.TAG_NAME,'dd').text)
                address.append(info.find_element(By.TAG_NAME,'dd').text)
    corp = []
    corp_name = driver.find_elements(By.CLASS_NAME,"company_popup")
    money_btn = []
    for i in range(len(corp_name)):
        corp_name[i].click()
        time.sleep(1)
        driver.switch_to.window( driver.window_handles[-1] )
        try:
            money_btn = driver.find_elements(By.CSS_SELECTOR,".btn_menu.ga_data_layer")
            money_btn[2].click()
            html = driver.page_source
            soup = BeautifulSoup(html, "html.parser")
            uni_money_al = soup.find("div",class_ = "content_gird univ")
            uni_money = uni_money_al.find("p", class_ = "salary").text
            uni_money=uni_money.replace(',','')
            uni_money=uni_money[:-2]
            uni_avg_list.append(int(uni_money))
            print(uni_money)
            
            age_list=[]
            age_salary_list=[]

            child = driver.find_element(By.ID,"info")
            driver.execute_script("arguments[0].scrollIntoView(false);", child)
            driver.find_element(By.CSS_SELECTOR,'#content > div > div.main_content.salary_view_wrap > div.box_company_view.salary_age > div > div.category_head > div > ul > li:nth-child(1) > button').click()
            time.sleep(1)
            select=driver.find_element(By.CLASS_NAME,'dot_group0')
            select_all=select.find_elements(By.CLASS_NAME,'dot')
            select_dot=select.find_element(By.CLASS_NAME,'dot')
            count=len(select_all)
            for i in range(0,count):
                draggable = select_dot
                droppable = select_dot
                action=ActionChains(driver)
                action.drag_and_drop(draggable, droppable)
                action.move_by_offset(25*i, 0)
                action.perform()
                time.sleep(1)
                age_salary=driver.find_element(By.ID,'lineCheartTooltip')
                age=age_salary.find_element(By.CLASS_NAME,'years').text
                salary=age_salary.find_element(By.CLASS_NAME,'salary').text
                age=int(age[:-1])
                salary=int(salary.replace(',',''))
                print(age)
                print(salary)
                age_list.append(age)
                age_salary_list.append(salary)
            
            all_age.append(age_list)
            print(all_age)
            all_salary.append(age_salary_list)
            print(all_salary)

            driver.close()
            driver.switch_to.window( driver.window_handles[0])
        except:
            driver.close()
            uni_avg_list.append(0)
            driver.switch_to.window( driver.window_handles[0])
        

import re
address_list=[]
for ads in address:
    match = re.search('([가-힣]+(?:[도]))\s([가-힣]+구)',ads)
    # 결과 출력
    if match:
        result = match.group(0)
        print(result)
        address_list.append(result)
    else:
        text = re.search('\w+\s\w+',ads).group(0)
        print(text)
        address_list.append(text)

(주)클로봇
(주)로보티즈
(주)마루에이치알
휴림로봇(주)
(주)세스텍
(주)미르이즈
(주)엠앤디
(주)아이지
(사)캠틱종합기술원
(주)페르소나에이아이
(주)트위니
(주)휴로틱스
두산로보틱스(주)
(주)인티그리트
빅웨이브로보틱스(주)
(주)럭스로보
(주)로아스
(주)링크솔루션
(주)베어로보틱스코리아
코가로보틱스(주)
경기 성남시 분당구 성남대로925번길 16, 7층 701호
서울 강서구 마곡중앙5로1길 37
서울 영등포구 경인로 775, 4동 5층 504호 (문래동3가,에이스하이테크시티)
충남 천안시 서북구 직산읍 4산단6길 27
충남 아산시 음봉면 월산로 134
서울 마포구 양화로 156, 1723호 (동교동,엘지팰리스빌딩)
서울 서초구 효령로34길 4, 2층 202호 (방배동,프린스효령빌딩)
경기 성남시 중원구 순환로198번길 7 (상대원동,아이지빌딩)
전북 전주시 덕진구 유상로 67, 전주첨단벤처단지
서울 강남구 삼성로 540, 2층 (삼성동,브로모빌딩)
대전 유성구 가정북로 90
서울 동작구 흑석로 84, 209관 204호 (흑석동,중앙대학교)
경기 수원시 권선구 산업로156번길 79
서울 강남구 삼성로 547, 5층 (삼성동,비케이타워)
서울 강남구 역삼로 542, 4층 (대치동,신사에스앤지빌딩)
서울 서초구 강남대로 311, 13층 (서초동,한화생명빌딩)
경기 안양시 동안구 엘에스로116번길 39, 엘에스엠트론 하이테크센타 사무동 402호
경기 안양시 동안구 부림로170번길 41-4, 5층 (관양동,디에스세미콘)
서울 성동구 성수일로 10, 11층 (성수동1가,서울숲아이티시티지식산업센터)
서울 성동구 왕십리로 222, 516호 (사근동,한양기술종합연구원 에이치아이티)
3999
20
3645
21
3645
22
3641
23
3842
24
3865
25
3986
26
4099
27
4230
28
4398
29
4551
30
4693
31
4852
32
5026
33
5203
34
5369
35
5511
36
5648
37
5797
38
5985
39


In [4]:
len(address_list),len(corp_name_list),len(uni_avg_list),len(address_list)

(369, 369, 369, 369)

In [44]:
n=[]
for ads in address_list:
    if ads[:2]=='서울':
        n.append(ads)
    elif ads[:2]=='경기':
        if ads[3:5]=='광주':
            n.append(ads[:5])
        else:
            n.append(ads[3:5])
    else:
        n.append(ads[:2])

In [45]:
data={
    'Company':corp_name_list,
    'AVG_salary':uni_avg_list,
    'Address':n
}
df=pd.DataFrame(data)
df.head()

Company  AVG_salary  Address
0     (주)클로봇        3999       성남
1    (주)로보티즈        3610   서울 강서구
2  (주)마루에이치알        2891  서울 영등포구
3    휴림로봇(주)        3219       충남
4     (주)세스텍        3795       충남

In [8]:
import folium
import json

with open('/home/sang/dev_ws/eda/data/json/map.json', encoding='utf-8') as file:
    korea_map = json.load(file)

address_counts = df['Address'].value_counts().reset_index()
address_counts.columns = ['Address', 'Count']

my_map=folium.Map(location=[37.5502,126.982],zoom_start=10)
folium.Choropleth(
    geo_data=korea_map,
    data=address_counts,
    fill_color='PuRd',
    key_on='feature.id',
    fill_opacity=0.7,
    line_opacity=0.2,
    columns=['Address','Count']
).add_to(my_map)
my_map

In [46]:
df.to_csv('../data/csv/saramin_info.csv',sep=',',encoding='utf-8')

In [10]:
address

['경기 성남시 분당구 성남대로925번길 16, 7층 701호',
 '서울 강서구 마곡중앙5로1길 37',
 '서울 영등포구 경인로 775, 4동 5층 504호 (문래동3가,에이스하이테크시티)',
 '충남 천안시 서북구 직산읍 4산단6길 27',
 '충남 아산시 음봉면 월산로 134',
 '서울 마포구 양화로 156, 1723호 (동교동,엘지팰리스빌딩)',
 '서울 서초구 효령로34길 4, 2층 202호 (방배동,프린스효령빌딩)',
 '경기 성남시 중원구 순환로198번길 7 (상대원동,아이지빌딩)',
 '전북 전주시 덕진구 유상로 67, 전주첨단벤처단지',
 '경기 성남시 분당구 판교로255번길 20 (삼평동,원익빌딩)',
 '서울 강남구 삼성로 540, 2층 (삼성동,브로모빌딩)',
 '대전 유성구 가정북로 90',
 '서울 동작구 흑석로 84, 209관 204호 (흑석동,중앙대학교)',
 '경기 수원시 권선구 산업로156번길 79',
 '서울 강남구 삼성로 547, 5층 (삼성동,비케이타워)',
 '서울 서초구 강남대로 311, 13층 (서초동,한화생명빌딩)',
 '서울 강남구 역삼로 542, 4층 (대치동,신사에스앤지빌딩)',
 '경기 안양시 동안구 엘에스로116번길 39, 엘에스엠트론 하이테크센타 사무동 402호',
 '경기 안양시 동안구 부림로170번길 41-4, 5층 (관양동,디에스세미콘)',
 '서울 성동구 성수일로 10, 11층 (성수동1가,서울숲아이티시티지식산업센터)',
 '서울 성동구 왕십리로 222, 516호 (사근동,한양기술종합연구원 에이치아이티)',
 '경기 성남시 분당구 대왕판교로395번길 8, A동',
 '부산 강서구 생곡로189번길 23',
 '경기 용인시 기흥구 기흥로 58-1, 제에이동 1306호',
 '인천 미추홀구 염전로 324',
 '광주 광산구 하남산단9번로 41',
 '대전 유성구 갑천로 361-39',
 '경기 성남시 수정구 창업로 42, 판교 제2테크노밸리 경기 기업성장센터 에프1블럭 9층 901호-904호',
 '

In [6]:
driver.switch_to.window( driver.window_handles[0] )
driver.find_element(By.CSS_SELECTOR,'#company_info_list > div.content > div:nth-child(1) > h2 > a').click()
driver.switch_to.window( driver.window_handles[-1] )
driver.find_element(By.CSS_SELECTOR,'#content> div > div.sidebar.recommendation > div > nav > ul > li:nth-child(3)').click()


ElementClickInterceptedException: Message: element click intercepted: Element <a href="/zf_user/company-info/view?csn=aTc1RVBIZklBZWU4Tzk1VGFWeFFIZz09" title="..." target="_blank" class="company_popup">(주)클로봇</a> is not clickable at point (88, 10). Other element would receive the click: <div class="navigation">...</div>
  (Session info: chrome=131.0.6778.204)
Stacktrace:
#0 0x55cb8654b8fa <unknown>
#1 0x55cb8605cd20 <unknown>
#2 0x55cb860b2766 <unknown>
#3 0x55cb860b06cd <unknown>
#4 0x55cb860adde5 <unknown>
#5 0x55cb860acfa8 <unknown>
#6 0x55cb860a0765 <unknown>
#7 0x55cb860cfaf2 <unknown>
#8 0x55cb860a00a8 <unknown>
#9 0x55cb860cfcbe <unknown>
#10 0x55cb860ee560 <unknown>
#11 0x55cb860cf893 <unknown>
#12 0x55cb8609e30d <unknown>
#13 0x55cb8609f32e <unknown>
#14 0x55cb8651800b <unknown>
#15 0x55cb8651bf97 <unknown>
#16 0x55cb8650471c <unknown>
#17 0x55cb8651cb17 <unknown>
#18 0x55cb864e96cf <unknown>
#19 0x55cb8653a6b8 <unknown>
#20 0x55cb8653a880 <unknown>
#21 0x55cb8654a776 <unknown

In [3]:
age_salary_click=driver.find_element(By.CLASS_NAME,'btn_age_statistics')
age_salary_click.click()


In [ ]:
draggable = driver.find_element(By.CLASS_NAME,'line_bar')
droppable = driver.find_element(By.CLASS_NAME,'line_bar')
action=ActionChains(driver)
action.drag_and_drop(draggable, droppable)
action.perform()
age_salary=driver.find_element(By.ID,'lineCheartTooltip')
age=age_salary.find_element(By.CLASS_NAME,'years').text
salary=age_salary.find_element(By.CLASS_NAME,'salary').text
print(age)
print(salary)

20세
3,645


In [5]:
age_list=[]
age_salary_list=[]

select=driver.find_element(By.CLASS_NAME,'dot_group0')
select_all=select.find_elements(By.CLASS_NAME,'dot')
select_dot=select.find_element(By.CLASS_NAME,'dot')
count=len(select_all)
for i in range(0,count):
    draggable = select_dot
    droppable = select_dot
    action=ActionChains(driver)
    action.drag_and_drop(draggable, droppable)
    action.move_by_offset(25*i, 0)
    action.perform()
    time.sleep(0.5)
    age_salary=driver.find_element(By.ID,'lineCheartTooltip')
    age=age_salary.find_element(By.CLASS_NAME,'years').text
    salary=age_salary.find_element(By.CLASS_NAME,'salary').text
    age=int(age[:-1])
    salary=int(salary.replace(',',''))
    print(age)
    print(salary)
    age_list.append(age)
    age_salary_list.append(salary)

20
3645
21
3645


KeyboardInterrupt: 

In [ ]:
print(driver.find_elements(By.CLASS_NAME,'line_bar'))

[<selenium.webdriver.remote.webelement.WebElement (session="4fb7b376c0505c43f2a3594eedaeb360", element="f.91710FF66B9DD0511F7DACAF2480313C.d.292EB6BC6635D62793872847EF5FC3A7.e.4733")>, <selenium.webdriver.remote.webelement.WebElement (session="4fb7b376c0505c43f2a3594eedaeb360", element="f.91710FF66B9DD0511F7DACAF2480313C.d.292EB6BC6635D62793872847EF5FC3A7.e.4734")>, <selenium.webdriver.remote.webelement.WebElement (session="4fb7b376c0505c43f2a3594eedaeb360", element="f.91710FF66B9DD0511F7DACAF2480313C.d.292EB6BC6635D62793872847EF5FC3A7.e.4735")>, <selenium.webdriver.remote.webelement.WebElement (session="4fb7b376c0505c43f2a3594eedaeb360", element="f.91710FF66B9DD0511F7DACAF2480313C.d.292EB6BC6635D62793872847EF5FC3A7.e.4736")>, <selenium.webdriver.remote.webelement.WebElement (session="4fb7b376c0505c43f2a3594eedaeb360", element="f.91710FF66B9DD0511F7DACAF2480313C.d.292EB6BC6635D62793872847EF5FC3A7.e.4737")>, <selenium.webdriver.remote.webelement.WebElement (session="4fb7b376c0505c43f2a3

In [29]:
data={
    'Age':all_age,
    'age_salary':all_salary
}
money=pd.DataFrame(data)
money.head()

Age  \
0  [20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 3...   
1  [20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 3...   
2  [20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 3...   
3  [20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 3...   
4  [20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 3...   

                                          age_salary  
0  [3645, 3645, 3641, 3842, 3865, 3986, 4099, 423...  
1  [3295, 3295, 3379, 3510, 3565, 3676, 3746, 382...  
2  [2579, 2579, 2695, 2769, 2839, 2948, 3013, 306...  
3  [2973, 2973, 2914, 3109, 3109, 3189, 3285, 340...  
4  [3639, 3639, 3611, 3825, 3830, 3915, 3969, 403...

In [38]:
len(all_salary),len(all_age),len(uni_avg_list)

(214, 214, 369)

In [39]:
money.to_csv('../data/salary_increase.csv',sep=',',encoding='utf-8')

In [47]:
df=pd.read_csv('../data/csv/saramin_info.csv')

In [48]:
df=df[df['AVG_salary']>0]
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 214 entries, 0 to 308
Data columns (total 4 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   Unnamed: 0  214 non-null    int64 
 1   Company     214 non-null    object
 2   AVG_salary  214 non-null    int64 
 3   Address     214 non-null    object
dtypes: int64(2), object(2)
memory usage: 8.4+ KB
